## WebDataset

The dataset can be exported to a `.tar` archive and iterated with the `webdataset`
package.

After building the WebDataset-formatted archives using `make webdataset`, the dataset can be iterated as follows.

In [1]:
import webdataset as wds
import json

from pprint import pformat
import os

# Create iterable dataset
shard_dir = "shards/val"
ds = wds.WebDataset([os.path.join(shard_dir, shard_file) for shard_file in os.listdir(shard_dir)], shardshuffle=False, verbose=True)

# Iterate over the dataset and print the keys and the first few samples
for i, sample in enumerate(ds):
    if i > 2:  
        break
    meta_data = json.loads(sample["frames.json"].decode())
    print("Sample " + sample["__key__"])
    print(pformat(meta_data, compact=True))
    

Sample csvps-val/000030
['000000', '000001', '000002', '000003', '000004', '000005', '000006', '000007',
 '000008', '000009', '000010', '000011', '000012', '000013', '000014', '000015',
 '000016', '000017', '000018', '000019', '000020', '000021', '000022', '000023',
 '000024', '000025', '000026', '000027', '000028', '000029']
Sample csvps-val/000031
['000000', '000001', '000002', '000003', '000004', '000005', '000006', '000007',
 '000008', '000009', '000010', '000011', '000012', '000013', '000014', '000015',
 '000016', '000017', '000018', '000019', '000020', '000021', '000022', '000023',
 '000024', '000025', '000026', '000027', '000028', '000029']
Sample csvps-val/000032
['000000', '000001', '000002', '000003', '000004', '000005', '000006', '000007',
 '000008', '000009', '000010', '000011', '000012', '000013', '000014', '000015',
 '000016', '000017', '000018', '000019', '000020', '000021', '000022', '000023',
 '000024', '000025', '000026', '000027', '000028', '000029']


### Sample frames

We can use `webdataset`'s compose helper to split the sequences into individual (pairs of) frames.

In [2]:
import collections
import itertools

def find_frame_keys(keys, frames):
    r"""
    Returns a mapping from frame number to the keys of the sample that correspond to 
    that frame.
    """
    meta_keys = set()
    frame_keys = collections.defaultdict(list)
    for key in keys:
        if key.startswith("__"):
            continue
        if "." not in key:
            meta_keys.add(key)
            continue 
        stem, other = key.split(".", 1)
        if stem in frames:
            frame_keys[stem].append(other)
        else:
            meta_keys.add(key)
    return dict(frame_keys), meta_keys


def generate_range(src, length: int = 2, *, missing_ok: bool =True):
    for sample in src:
        frames = json.loads(sample.pop("frames.json").decode())
        key = sample["__key__"]
        frame_keys, meta_keys = find_frame_keys(sample.keys(), frames) 
        
        pair_keys = set(itertools.chain.from_iterable(frame_keys.values()))
        meta_data = {key: sample[key] for key in meta_keys}

        frame_ids = list(frame_keys.keys())

        for i in range(0, len(frame_keys) - length):
            ids = frame_ids[i:i + length]

            pair_data = {
                "__key__": f"{key}/{ids[0]}:{ids[-1]}" if len(ids) > 1 else f"{key}/{ids[0]}",
                **meta_data,
                **{
                    source_key: [sample.get(f"{frame}.{source_key}", None) for frame in ids]
                    for source_key in pair_keys
                }
            }

            yield pair_data

ds_per_frame = ds.compose(generate_range)

sample = next(iter(ds_per_frame))

for key, value in sample.items():
    print(f"{key} ({type(value)})", end=" ")
    if isinstance(value, list):
        print(len(value))
    elif isinstance(value, bytes):
        print("...")
    else:
        print(value)


__key__ (<class 'str'>) csvps-val/000030/000000:000001
camera.json (<class 'bytes'>) ...
metadata.json (<class 'list'>) 2
vehicle.json (<class 'list'>) 2
image.png (<class 'list'>) 2
panoptic.png (<class 'list'>) 2
depth.tiff (<class 'list'>) 2


## Hugging Face Datasets

The WebDataset can be used directly in Hugging Face Datasets.

In [ ]:
import datasets

dataset = datasets.load_dataset("webdataset", data_dir="shards", split="train")
print(dataset)


Resolving data files:   0%|          | 0/40 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

DatasetGenerationError: An error occurred while generating the dataset